In [1]:
import yfinance as yf
import numpy as np
import pandas as pd
import datetime as dt
import math

def get_data(stocks, start, end):
    stock_data = yf.download(stocks, start=start, end=end)['Adj Close']
    returns = stock_data.pct_change().dropna()
    #returns a DataFrame with the percentage difference between the values for each row and, by default, the previous row.
    meanreturns = returns.mean()
    covmatrix = returns.cov()
    
    return returns, meanreturns, covmatrix

stocks = ['ADANIPORTS.NS', 'TCS.NS', 'INFY.NS', 'BAJFINANCE.NS', 'INFY.NS'] 
end_date = dt.datetime.now()
start_date = end_date - dt.timedelta(days=1000) 

returns, meanreturns, covmatrix = get_data(stocks, start=start_date, end=end_date)


C:\Users\Puneeth G B\anaconda3\lib\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


[*********************100%***********************]  4 of 4 completed


C:\Users\Puneeth G B\anaconda3\lib\site-packages\yfinance\utils.py:689: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
C:\Users\Puneeth G B\anaconda3\lib\site-packages\yfinance\utils.py:689: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
C:\Users\Puneeth G B\anaconda3\lib\site-packages\yfinance\utils.py:689: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed in a future version. Use pd.to_timedelta instead.
  df.index += _pd.TimedeltaIndex(dst_error_hours, 'h')
C:\Users\Puneeth G B\anaconda3\lib\site-packages\yfinance\utils.py:689: FutureWarning: The 'unit' keyword in TimedeltaIndex construction is deprecated and will be removed i

In [2]:
def portfolioPerformance(weights, meanreturns, covmatrix, time):
    returns = np.sum(meanreturns*weights)*time
    std = np.sqrt( np.dot(weights.T, np.dot(covmatrix, weights)) ) * np.sqrt(time)
    return returns, std

In [3]:
print(returns)
print(len(returns))
print(returns.shape)
print(returns.info())
print(returns.describe())

            ADANIPORTS.NS  BAJFINANCE.NS   INFY.NS    TCS.NS
Date                                                        
2022-02-08       0.003706       0.017949  0.001341 -0.009407
2022-02-09       0.021803       0.008838  0.011646  0.004568
2022-02-10      -0.003272       0.002761  0.018592  0.002606
2022-02-11      -0.010054      -0.017570 -0.027266 -0.019998
2022-02-14      -0.038621      -0.032182 -0.022744  0.010501
...                   ...            ...       ...       ...
2024-10-28       0.025404       0.000174  0.001772  0.008207
2024-10-29       0.015160       0.016082 -0.002738 -0.003813
2024-10-30       0.017120      -0.009612 -0.020225  0.002307
2024-10-31      -0.014504      -0.009382 -0.024888 -0.028448
2024-11-01       0.000000       0.000000  0.000000  0.000000

[675 rows x 4 columns]
675
(675, 4)
<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 675 entries, 2022-02-08 to 2024-11-01
Data columns (total 4 columns):
 #   Column         Non-Null Count  Dtype  
---

In [4]:
returns = returns.dropna()

weights = np.random.random(len(returns.columns))
weights

array([0.48659927, 0.07699603, 0.24116177, 0.59958397])

In [5]:
weights /= np.sum(weights)

returns['portfolio'] = returns.dot(weights)

In [6]:
def historicalVAR(returns,alpha=5):
    if isinstance(returns,pd.Series):
        return np.percentile(returns,alpha)
    elif isinstance(returns,pd.DataFrame):
        return returns.aggregate(historicalVAR,alpha=alpha)
    else:
        return TypeError("Expected returns to be dataframe or series")

In [7]:
def historicalCVAR(returns,alpha=5):
    if isinstance(returns,pd.Series):
        belowVAR = returns <=historicalVAR(returns,alpha=alpha)
        return returns[belowVAR].mean()
    elif isinstance(returns,pd.DataFrame):
        return returns.aggregate(historicalCVAR,alpha=alpha)
    else:
        return TypeError("Expected returns to be dataframe or series")

In [8]:
time = 100

In [9]:
hVAR = -historicalVAR(returns['portfolio'],alpha=5)*np.sqrt(time)
hCVAR = -historicalCVAR(returns['portfolio'],alpha=5)*np.sqrt(time)
pret,pstd = portfolioPerformance(weights,meanreturns,covmatrix,time)

In [10]:
InitialInvestment = 10000
print('Expected Portfolio Return:      ', round(InitialInvestment*pret,2))
print('Value at Risk 95th CI    :      ', round(InitialInvestment*hVAR,2))
print('Conditional VaR 95th CI  :      ', round(InitialInvestment*hCVAR,2))

Expected Portfolio Return:       620.55
Value at Risk 95th CI    :       1988.28
Conditional VaR 95th CI  :       3147.31


In [11]:
from scipy.stats import norm, t
def var_parametric(portofolioReturns, portfolioStd, distribution='normal', alpha=5, dof=6):
    # because the distribution is symmetric
    if distribution == 'normal':
        VaR = norm.ppf(1-alpha/100)*portfolioStd - portofolioReturns
    elif distribution == 't-distribution':
        nu = dof
        VaR = np.sqrt((nu-2)/nu) * t.ppf(1-alpha/100, nu) * portfolioStd - portofolioReturns
    else:
        raise TypeError("Expected distribution type 'normal'/'t-distribution'")
    return VaR

In [12]:
def cvar_parametric(portofolioReturns, portfolioStd, distribution='normal', alpha=5, dof=6):
    if distribution == 'normal':
        CVaR = (alpha/100)**-1 * norm.pdf(norm.ppf(alpha/100))*portfolioStd - portofolioReturns
    elif distribution == 't-distribution':
        nu = dof
        xanu = t.ppf(alpha/100, nu)
        CVaR = -1/(alpha/100) * (1-nu)**(-1) * (nu-2+xanu**2) * t.pdf(xanu, nu) * portfolioStd - portofolioReturns
    else:
        raise TypeError("Expected distribution type 'normal'/'t-distribution'")
    return CVaR

In [13]:
normVaR = var_parametric(pret,pstd)
normCVaR = cvar_parametric(pret,pstd)

In [14]:
tVaR = var_parametric(pret,pstd,distribution='t-distribution')
tCVaR = cvar_parametric(pret,pstd,distribution='t-distribution')

In [15]:
print("Normal VaR 95th CI       :      ", round(InitialInvestment*normVaR,2))
print("Normal CVaR 95th CI      :      ", round(InitialInvestment*normCVaR,2))
print("t-dist VaR 95th CI       :      ", round(InitialInvestment*tVaR,2))
print("t-dist CVaR 95th CI      :      ", round(InitialInvestment*tCVaR,2))

Normal VaR 95th CI       :       1600.12
Normal CVaR 95th CI      :       2164.27
t-dist VaR 95th CI       :       1521.48
t-dist CVaR 95th CI      :       2290.43


In [16]:
mc_sims = 400
t=100

meanm = np.full(shape=(t,len(weights)),fill_value=meanreturns)

In [17]:
meanm = meanm.T

In [18]:
portfolio_sims = np.full(shape=(t,mc_sims),fill_value=0.0)

In [19]:
initialportfolio = 10000

In [20]:
import random
for m in range(0,mc_sims):
    z = np.random.normal(size=(t,len(weights)))
    l = np.linalg.cholesky(covmatrix)
    dailyreturns = meanm+np.inner(l,z)
    portfolio_sims[:,m]=np.cumprod(np.inner(weights,dailyreturns.T)+1)*initialportfolio

In [21]:
import plotly.express as px
fig = px.line(portfolio_sims, title='MC Simulation of a Stock Portfolio').update_layout(xaxis_title='Days', yaxis_title='Portfolio Value ($)',showlegend=False)
fig.show()

C:\Users\Puneeth G B\anaconda3\lib\site-packages\plotly\express\_core.py:1222: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_output[col_name] = to_unindexed_series(df_input[argument])
C:\Users\Puneeth G B\anaconda3\lib\site-packages\plotly\express\_core.py:1222: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_output[col_name] = to_unindexed_series(df_input[argument])
C:\Users\Puneeth G B\anaconda3\lib\site-packages\plotly\express\_core.py:1222: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result o

In [22]:
def mcvar(returns,alpha=5):
    if isinstance(returns,pd.Series):
        return np.percentile(returns,alpha)
    else: 
        return TypeError("Expected a pandas data series")

def mccvar(returns,alpha=5):
    if isinstance(returns,pd.Series):
        belowvar = returns <= mcvar(returns,alpha=alpha)
        return returns[belowvar].mean()
    else:
        raise TypeError("Expected a pandas data series")

In [23]:
portResults = pd.Series(portfolio_sims[-1,:])

VaR = initialportfolio - mcvar(portResults, alpha=5)
CVaR = initialportfolio - mccvar(portResults, alpha=5)

print('VaR ${}'.format(round(VaR,2)))
print('CVaR ${}'.format(round(CVaR,2)))

VaR $1441.33
CVaR $2028.1


In [24]:
print("\nVaR:")

print(' historical VaR 95th CI   :      ', round(InitialInvestment*hVAR,2))
print(" Normal VaR 95th CI       :      ", round(InitialInvestment*normVaR,2))
print(" t-dist VaR 95th CI       :      ", round(InitialInvestment*tVaR,2))
print(" MC VaR  95th CI          :      ", round(VaR,2))


print("\nCVaR:")

print(' historical CVaR 95th CI  :      ', round(InitialInvestment*hCVAR,2))
print(" Normal CVaR 95th CI      :      ", round(InitialInvestment*normCVaR,2))
print(" t-dist CVaR 95th CI      :      ", round(InitialInvestment*tCVaR,2))
print(" MC CVaR 95th CI          :      ", round(CVaR,2))
     


VaR:
 historical VaR 95th CI   :       1988.28
 Normal VaR 95th CI       :       1600.12
 t-dist VaR 95th CI       :       1521.48
 MC VaR  95th CI          :       1441.33

CVaR:
 historical CVaR 95th CI  :       3147.31
 Normal CVaR 95th CI      :       2164.27
 t-dist CVaR 95th CI      :       2290.43
 MC CVaR 95th CI          :       2028.1
